In [1]:
import numpy as np
import plotly.express as px

import os
from cmdstanpy import CmdStanModel, cmdstan_path

import git
git_root = git.Repo(search_parent_directories=True).git.rev_parse("--show-toplevel")

In [2]:
varying_file = os.path.join(git_root, 'src', 'models', 'stan', 'varying.stan')
varying_model = CmdStanModel(stan_file = varying_file)

In [3]:
n_people = 10
n_chocs = 17

np.random.seed(123)

choc_mus_true = np.random.normal(0, 1, n_chocs)[np.newaxis,:]
choc_sigmas_true = np.random.gamma(5, 0.1, size=n_chocs)[np.newaxis,:]

choc_ratings_true = np.random.normal(choc_mus_true,
                                     choc_sigmas_true,
                                     size=(n_people,
                                     n_chocs))

choc_rankings_true = np.argsort(choc_ratings_true, axis=1)

In [4]:
varying_fit = varying_model.sample(data={'n_people': n_people,
                                        'n_chocs': n_chocs,
                                        'rankings': (choc_rankings_true).astype('int')})

23:36:18 - cmdstanpy - INFO - CmdStan start processing


chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

23:36:45 - cmdstanpy - INFO - CmdStan done processing.
23:36:45 - cmdstanpy - WARNING - Non-fatal error during sampling:
Exception: gamma_lpdf: Random variable is -0.269047, but must be positive finite! (in '/home/jimmyclowes85/code/choc-ranking/src/models/stan/varying.stan', line 35, column 4 to column 36)
	Exception: gamma_lpdf: Random variable is -13.3087, but must be positive finite! (in '/home/jimmyclowes85/code/choc-ranking/src/models/stan/varying.stan', line 36, column 4 to column 38)
	Exception: gamma_lpdf: Random variable is -11.1015, but must be positive finite! (in '/home/jimmyclowes85/code/choc-ranking/src/models/stan/varying.stan', line 36, column 4 to column 38)
	Exception: gamma_lpdf: Random variable is -1.44985, but must be positive finite! (in '/home/jimmyclowes85/code/choc-ranking/src/models/stan/varying.stan', line 36, column 4 to column 38)
	Exception: gamma_lpdf: Random variable[3] is inf, but must be positive finite! (in '/home/jimmyclowes85/code/choc-ranking/src/

23:36:46 - cmdstanpy - WARNING - Some chains may have failed to converge.
	Chain 2 had 2 divergent transitions (0.2%)
	Chain 3 had 5 divergent transitions (0.5%)
	Use function "diagnose()" to see further information.


In [5]:
fig = px.violin(varying_fit.stan_variable('choc_mus_fitted'))
for i in range(0, n_chocs):

    fig.add_shape(
        type='line',
        x0=(i-0.5),
        y0=(choc_mus_true[0,i]),
        x1=i+0.5,
        y1=(choc_mus_true[0,i]),
        line=dict(
            color='Red',
        )
    )


fig.update_layout(
{
'plot_bgcolor': 'rgba(0, 0, 0, 0)',
'paper_bgcolor': 'rgba(0, 0, 0, 0)'
},
showlegend=False)

fig.update_xaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='chocolate')
fig.update_yaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='underling preference')

fig.show()

In [6]:
fig = px.violin(varying_fit.stan_variable('choc_sigmas_fitted'))
for i in range(0, n_chocs):

    fig.add_shape(
        type='line',
        x0=(i-0.5),
        y0=(choc_sigmas_true[0,i]),
        x1=i+0.5,
        y1=(choc_sigmas_true[0,i]),
        line=dict(
            color='Red',
        )
    )


fig.update_layout(
{
'plot_bgcolor': 'rgba(0, 0, 0, 0)',
'paper_bgcolor': 'rgba(0, 0, 0, 0)'
},
showlegend=False)

fig.update_xaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='chocolate')
fig.update_yaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='variation in preferences')

fig.show()